# Station Catchment Buildings EDA

이 노트북은 `Station_Catchment_Buildings` 테이블의 데이터를 탐색하고 시각화합니다.
역세권 내 건물의 용도, 구조, 높이, 연면적 등의 특성을 분석합니다.

In [37]:
import sqlite3
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
from IPython.display import display

# 설정
DB_PATH = "../db/subway.db"

def get_connection():
    return sqlite3.connect(DB_PATH)

## 1. 데이터 로드

데이터베이스에서 `Station_Catchment_Buildings` 테이블과 `Stations` 테이블을 조인하여 데이터를 가져옵니다.

In [38]:
conn = get_connection()

query = """
SELECT 
    b.*, 
    s.station_name_kr
FROM Station_Catchment_Buildings b
JOIN Stations s ON b.station_id = s.station_id
"""

df = pd.read_sql(query, conn)
conn.close()

print(f"Total Rows: {len(df)}")
display(df.head())

Total Rows: 412405


id  station_id building_name building_detail_name usage_type  \
0   1           7          None                 None       단독주택   
1   2           7          None                 None       단독주택   
2   3         178          None                 None       단독주택   
3   4         178          None                 None       단독주택   
4   5         178          None                 None       단독주택   

  structure_type approval_date  height  floor_area  households  families  \
0          기타강구조    1991-09-02     9.1   144.66202         3.0       0.0   
1          기타강구조    1991-09-02     9.1   144.66202         3.0       0.0   
2           벽돌구조    1967-05-28     0.0     0.00000         3.0       0.0   
3           벽돌구조    1962-12-21     0.0     0.00000         2.0       0.0   
4           벽돌구조    1979-06-01     0.0     0.00000         2.0       1.0   

  station_name_kr  
0             신설동  
1             신설동  
2              창신  
3              창신  
4              창신

## 2. 기본 정보 확인

데이터 타입과 결측치를 확인합니다.

In [39]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 412405 entries, 0 to 412404
Data columns (total 12 columns):
 #   Column                Non-Null Count   Dtype  
---  ------                --------------   -----  
 0   id                    412405 non-null  int64  
 1   station_id            412405 non-null  int64  
 2   building_name         56569 non-null   object 
 3   building_detail_name  29124 non-null   object 
 4   usage_type            328376 non-null  object 
 5   structure_type        328276 non-null  object 
 6   approval_date         316885 non-null  object 
 7   height                412314 non-null  float64
 8   floor_area            411890 non-null  float64
 9   households            412368 non-null  float64
 10  families              411977 non-null  float64
 11  station_name_kr       412405 non-null  object 
dtypes: float64(4), int64(2), object(6)
memory usage: 37.8+ MB


In [40]:
display(df.describe())

id     station_id         height     floor_area  \
count  412405.00000  412405.000000  412314.000000  411890.000000   
mean   206203.00000     106.046806       6.178998      84.530353   
std    119051.21322      73.739097      10.597383     116.479762   
min         1.00000       1.000000       0.000000       0.000000   
25%    103102.00000      40.000000       0.000000       0.000000   
50%    206203.00000      99.000000       0.000000       0.000000   
75%    309304.00000     172.000000      10.600000     165.340000   
max    412405.00000     251.000000     902.000000    6480.060000   

          households       families  
count  412368.000000  411977.000000  
mean        2.764870       0.567119  
std         3.079715       0.659812  
min         0.000000       0.000000  
25%         1.000000       0.000000  
50%         2.000000       1.000000  
75%         4.000000       1.000000  
max        69.000000      10.000000

### 결측치 시각화

In [41]:
missing_counts = df.isnull().sum()
missing_percent = (missing_counts / len(df)) * 100

fig = go.Figure(data=[go.Bar(
    x=missing_percent.index,
    y=missing_percent.values,
    text=missing_percent.values.round(1),
    textposition='auto'
)])

fig.update_layout(
    title="컬럼별 결측치 비율 (%)",
    xaxis_title="컬럼",
    yaxis_title="결측치 비율 (%)",
    yaxis_range=[0, 100]
)

fig.show()

## 3. 단변량 분석 (Univariate Analysis)

### 건물 주용도 (Usage Type) 분포

In [42]:
usage_counts = df['usage_type'].value_counts().head(20)

fig = go.Figure(data=[go.Bar(
    x=usage_counts.index,
    y=usage_counts.values,
    marker_color='royalblue'
)])

fig.update_layout(
    title="건물 주용도 상위 20개 분포",
    xaxis_title="주용도",
    yaxis_title="건물 수",
    xaxis_tickangle=-45
)

fig.show()

### 건물 구조 (Structure Type) 분포

In [43]:
structure_counts = df['structure_type'].value_counts().head(20)

fig = go.Figure(data=[go.Bar(
    x=structure_counts.index,
    y=structure_counts.values,
    marker_color='crimson'
)])

fig.update_layout(
    title="건물 구조 상위 20개 분포",
    xaxis_title="구조",
    yaxis_title="건물 수",
    xaxis_tickangle=-45
)

fig.show()

### 건물 높이 (Height) 분포
높이가 0이거나 결측치인 경우는 제외하고 시각화합니다.

In [44]:
height_data = df[df['height'] > 0]['height']

fig = go.Figure(data=[go.Histogram(
    x=height_data,
    nbinsx=100,
    marker_color='green'
)])

fig.update_layout(
    title="건물 높이 분포 (0m 초과)",
    xaxis_title="높이 (m)",
    yaxis_title="빈도",
    xaxis_range=[0, 100] # 대부분의 건물이 저층일 수 있으므로 줌인
)

fig.show()

### 연면적 (Floor Area) 분포

In [45]:
area_data = df[df['floor_area'] > 0]['floor_area']

fig = go.Figure(data=[go.Histogram(
    x=area_data,
    nbinsx=200,
    marker_color='orange'
)])

fig.update_layout(
    title="건물 연면적 분포 (0 초과)",
    xaxis_title="연면적 (m²)",
    yaxis_title="빈도",
    xaxis_type="log" # 편차가 크므로 로그 스케일 사용 고려
)

fig.show()

## 4. 이변량 분석 (Bivariate Analysis)

### 역별 건물 수 Top 20

In [46]:
station_counts = df['station_name_kr'].value_counts().head(20)

fig = go.Figure(data=[go.Bar(
    x=station_counts.index,
    y=station_counts.values,
    marker_color='purple'
)])

fig.update_layout(
    title="역세권 내 건물 수가 많은 역 Top 20",
    xaxis_title="역명",
    yaxis_title="건물 수",
    xaxis_tickangle=-45
)

fig.show()

### 역별 평균 건물 높이 Top 20

In [47]:
station_avg_height = df[df['height'] > 0].groupby('station_name_kr')['height'].mean().sort_values(ascending=False).head(20)

fig = go.Figure(data=[go.Bar(
    x=station_avg_height.index,
    y=station_avg_height.values,
    marker_color='teal'
)])

fig.update_layout(
    title="역세권 평균 건물 높이가 높은 역 Top 20",
    xaxis_title="역명",
    yaxis_title="평균 높이 (m)",
    xaxis_tickangle=-45
)

fig.show()

## 3. 건물 주용도 (`usage_type`) 분석

역세권 내 건물의 주용도 분포를 분석합니다.

In [48]:
usage_counts = df['usage_type'].value_counts().head(20)
display(usage_counts)

usage_type
단독주택          151334
공동주택           59241
제2종근린생활시설      49854
제1종근린생활시설      43844
업무시설            8087
교육연구시설          3765
숙박시설            2303
공장              1581
종교시설            1476
노유자시설           1444
창고시설             928
판매시설             828
자동차관련시설          822
문화및집회시설          607
근린생활시설           599
의료시설             512
위험물저장및처리시설       346
위락시설             247
운동시설             129
방송통신시설            93
Name: count, dtype: int64

In [49]:
fig = go.Figure(data=[go.Bar(
    x=usage_counts.index,
    y=usage_counts.values,
    marker_color='indianred'
)])

fig.update_layout(
    title="역세권 건물 주용도 Top 20",
    xaxis_title="용도",
    yaxis_title="건물 수",
    xaxis_tickangle=-45
)

fig.show()

## 4. 세대수 및 가구수 분석

역세권 내 건물의 세대수와 가구수 분포를 분석합니다.
세대수(Households)는 법적인 세대 단위를 의미하며, 가구수(Families)는 실제 거주하는 가구 단위를 의미할 수 있습니다 (데이터 정의에 따라 상이할 수 있음).

In [50]:
print("세대수 기술통계:")
display(df['households'].describe())

print("\n가구수 기술통계:")
display(df['families'].describe())

세대수 기술통계:


count    412368.000000
mean          2.764870
std           3.079715
min           0.000000
25%           1.000000
50%           2.000000
75%           4.000000
max          69.000000
Name: households, dtype: float64


가구수 기술통계:


count    411977.000000
mean          0.567119
std           0.659812
min           0.000000
25%           0.000000
50%           1.000000
75%           1.000000
max          10.000000
Name: families, dtype: float64

In [51]:
# 세대수가 0인 경우는 제외하고, 분포를 확인하기 위해 상위 1% 이상치 제거 후 시각화
valid_households = df[df['households'] > 0]
upper_limit = valid_households['households'].quantile(0.99)
filtered_households = valid_households[valid_households['households'] < upper_limit]

fig = go.Figure()
fig.add_trace(go.Histogram(x=filtered_households['households'], name='세대수', nbinsx=30))

fig.update_layout(
    title=f"건물별 세대수 분포 (상위 1% 제외, Max: {upper_limit})",
    xaxis_title="세대수",
    yaxis_title="빈도",
    bargap=0.1
)
fig.show()

In [52]:
# 연면적과 세대수의 상관관계 (양의 상관관계 예상)
# 데이터가 많으므로 샘플링하여 시각화
sample_df = df[(df['floor_area'] > 0) & (df['households'] > 0)].sample(10000, random_state=42)

fig = go.Figure(data=go.Scatter(
    x=sample_df['floor_area'],
    y=sample_df['households'],
    mode='markers',
    marker=dict(
        size=5,
        color=sample_df['households'],
        colorscale='Viridis',
        showscale=True
    ),
    text=sample_df['building_name']
))

fig.update_layout(
    title="연면적 vs 세대수 (Sample 10,000)",
    xaxis_title="연면적 (m²)",
    yaxis_title="세대수",
    xaxis_type="log", # 로그 스케일 적용
    yaxis_type="log"
)
fig.show()